In [1]:
import numpy as np
import pandas as pd
import os
import sys
import pickle as pkl
import matplotlib.pyplot as plt
import plotly
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go
from scipy.ndimage import gaussian_filter
from scipy.spatial import KDTree

sys.setrecursionlimit(10000)
%matplotlib inline
init_notebook_mode(connected=True)

pd.options.mode.chained_assignment = None # turn off SettingWithCopyWarning

# Load & Filter Data

In [2]:
names = ["event_id", "user_id", "location_id", "lon", "lat", "epoch_time", "day_id", "seconds_since_monday"]

# USER SPECIFIC IMPORT
# directory = "C:\\Users\\alexj\\Documents\\Research\\twitter\\parcel_ass\\oc\\"  # alex
# directory = os.path.join("~", "dev", "CSAFE", "spatial-assocr", "data", "parcel_ass", "oc")  # chris
# events = pd.read_csv(directory + "ass_events.csv", header = None, names = names)
# data = pd.read_csv(os.path.join(directory, "ass_events_no_filter.csv"), header = None, names = names)


# GENERIC IMPORT (using files in the repo)
directory = os.path.join("..", "data")  # generic
data = pd.read_csv(os.path.join(directory, "parcel_ass-oc-ass_events_no_filter.csv"), header = None, names = names)

In [3]:
data.describe()

event_id       user_id    location_id            lon  \
count  6.559170e+05  6.559170e+05  655917.000000  655917.000000   
mean   6.319007e+06  7.921562e+08  241633.977727    -117.878281   
std    3.652273e+06  1.001908e+09  191189.068282       0.097180   
min    8.000000e+01  2.940000e+02       9.000000    -118.115560   
25%    3.156263e+06  5.413332e+07   61905.000000    -117.922940   
50%    6.301512e+06  2.876739e+08  211459.000000    -117.911910   
75%    9.483557e+06  1.219463e+09  409421.000000    -117.837490   
max    1.272555e+07  4.724669e+09  661044.000000    -117.446930   

                 lat    epoch_time         day_id  seconds_since_monday  
count  655917.000000  6.559170e+05  655917.000000         655917.000000  
mean       33.740011  1.441100e+09     114.426144         324717.879480  
std         0.104993  5.944586e+06      68.802527         174493.396071  
min        33.388260  1.431313e+09       1.000000              2.000000  
25%        33.665890  1.436230e+09      58.000000         162146.000000  
50%        33.778800  1.440782e+09     111.000000         330765.000000  
75%        33.811010  1.446231e+09     174.000000         481287.000000  
max        33.945950  1.452279e+09     244.000000         604798.000000

In [4]:
# round lat, long pairs to fall into discrete bins
data["lat_r"] = data.lat.round(3)
data["lon_r"] = data.lon.round(3)

In [5]:
# calculate counts for heatmap
freqs = data.groupby(['lat_r', 'lon_r']).count().reset_index()[["lat_r", "lon_r", "event_id"]]
freqs.columns = ["lat_r", "lon_r", "freq"]

In [6]:
# heatmap table
p_freqs = freqs.pivot_table(columns="lon_r", index="lat_r", values="freq", fill_value=0)

In [7]:
# remap user id for easier handling
user_dict = {}
index = 0
for ident in data.user_id.unique():
    if ident not in user_dict:
        user_dict[ident] = index
        index += 1

data["new_user_id"] = data.user_id.apply(lambda x: user_dict[x])

# reset day id to start at 0
data["day_id"] = data["day_id"] - data['day_id'].min()

In [8]:
# calculate week and month ids
data["week"] = data.day_id // 7
data['month'] = data.day_id // 30

# determine if you want to plot based on weeks or months
time_used = "month"  # "week" 

In [9]:
# calculate the number of events within each time period per user
counts2 = data.groupby(["new_user_id", time_used]).count()["event_id"]

In [10]:
# filter based on minimum amount of events per time period (n_k)
n_k = 50 # 35
view = counts2[counts2 > n_k].reset_index()

In [11]:
# join together to have a row for each user for a single week joined with the prior and next week
lagged_view = pd.concat([view, view.shift(1), view.shift(2)], axis = 1)
lagged_view.columns = list("next_" + view.columns) + list(view.columns) + list("last_" + view.columns)

In [12]:
# filter rows so that they only contain pairs where there is a sequential week present
right_users = (lagged_view["new_user_id"] == lagged_view["next_new_user_id"]) | (lagged_view["new_user_id"] == lagged_view["last_new_user_id"])
sequential = ((lagged_view["next_"+time_used] - lagged_view[time_used]) == 1) | ((lagged_view[time_used] - lagged_view["last_"+time_used]) == 1)
filtered = lagged_view[right_users & sequential][["new_user_id", time_used, "event_id"]].reset_index(drop=True)
filtered.head()

new_user_id  month  event_id
0          1.0    0.0     918.0
1          1.0    1.0    1044.0
2          1.0    2.0    1450.0
3          1.0    3.0    1586.0
4          1.0    4.0    1075.0

In [13]:
# gather ids and valid weeks for the users that have survived the filtering
user_time_dict = {-1 : []}
for i, x in filtered.iterrows():
    user_id = x["new_user_id"]
    time = x[time_used]
    if user_id not in user_time_dict:
        user_time_dict[user_id] = []
    user_time_dict[user_id].append(time)

In [14]:
# reduce the original data to be only valid events
reduced_view = pd.merge(left=filtered, right=data, on=["new_user_id", time_used], how="left")

In [15]:
# number of weeks available for analysis
sum([len(v) for k,v in user_time_dict.items()])

722

In [16]:
def get_user(id, time):
    return reduced_view[(reduced_view["new_user_id"] == id) & (reduced_view[time_used] == time)].reset_index(drop=True)

def make_user_scatter_plot(id, time):
    user = get_user(id, time)
    name = "{}-{}{}-{}".format(id, time_used[0], int(time), len(user))
    return go.Scatter(
        x = user.lon,
        y = user.lat,
        mode = 'markers',
        name = name,
        visible = "legendonly"
    )

def plot_figure(user_id):
    heat = go.Heatmap(
        z = gaussian_filter(p_freqs.values, sigma = 0.5).tolist(),
        x = p_freqs.columns,
        y = p_freqs.index,
        colorscale = [
            [0, 'rgb(0, 0, 0)'],        #0
            [1./10000, 'rgb(0, 0, 0)'],
            [1./10000, 'rgb(100, 100, 100)'], #10
            [1./1000, 'rgb(130, 130, 130)'],  #100
            [1./100, 'rgb(170, 170, 170)'],   #1000
            [1./10, 'rgb(220, 220, 220)'],       #10000
            [1., 'rgb(255, 255, 255)'],             #100000

        ],
        colorbar = {
            'tick0': 0,
            'tickmode': 'array',
            'tickvals': [0, 1000, 10000, 100000]
        }
    )

    traces = [heat]
    traces += [make_user_scatter_plot(user_id, time) for time in user_time_dict[user_id]]

    layout = go.Layout(
        legend=dict(x=-.35, y=1)
    )
    fig = go.Figure(data=traces, layout=layout)

    iplot(fig, show_link=False)

In [17]:
#### heatmap only
# -1
#
#### examples
# w: 1358 - concentrated
# w: 907  - very concentrated
# w: 1121 - scattered
# w: 1296 - very concentrated
# w: 13   - clustered w/ outliers
# m: 1409 - identical overlays
# m: 1587 - some clustering
# m: 1725 - extreme clustering
# 
# plot_figure(518)

# Inter-event Distance Exploration

Let's consider the first two months of data and users with at least $n_k = 50$ events in each month.

In [18]:
keep = []
for uid, months in user_time_dict.items():
    if all(x in months for x in [0., 1.]):
        keep.append(uid)
keep = keep[1:]  # uid 1 has ~2k events in only 2 locations
print("{} users have at least {} events in each of the first two months (month 0 and 1).".format(len(keep), n_k))

75 users have at least 50 events in each of the first two months (month 0 and 1).


In [19]:
# create a dataframe contianing the data to be analyzed
mpp = reduced_view.loc[(reduced_view['new_user_id'].isin(keep)) & (reduced_view['month'].isin({0., 1.})),].reset_index()
mpp['m'] = np.where(mpp['month'] == 0., 'a', 'b')
mpp = mpp[['new_user_id', 'm', 'lon', 'lat']].rename(index=str, columns={"new_user_id": "id"})

filepath = os.path.join("..", "data", "mpp_month0a_month1b_n50.csv")
mpp.to_csv(filepath, index=False)


In [20]:
def kdnearest(data, leafsize=10):
    """
    Measure the Haversine distance from each point in A 
    to its nearest neighbor in B using a KDTree data struct
    built from the locations in B.
    
    Params:
        data: pandas.DataFrame containing <'m', 'lat', 'lon'>
        leafsize: int specifing the number of data points to 
            place in each leaf node of the KDTree
    Returns:
        pandas.DataFrame of distances in km
    """
    data_copy = data.copy()
    R = 6371  # radius of earth in km
    
    def dist_to_arclength(chord_length):
        """
        https://en.wikipedia.org/wiki/Great-circle_distance
        Convert Euclidean chord length to great circle arc length
        """
        central_angle = 2*np.arcsin(chord_length/(2.0*R)) 
        arclength = R*central_angle
        return arclength

    # convert to Cartesian coordinates
    phi = np.deg2rad(data_copy['lat'])
    theta = np.deg2rad(data_copy['lon'])
    data_copy['x'] = R * np.cos(phi) * np.cos(theta)
    data_copy['y'] = R * np.cos(phi) * np.sin(theta)
    data_copy['z'] = R * np.sin(phi)
    
    # build the tree and query it  
    A = data_copy.loc[data_copy['m'] == 'a', ]  
    B = data_copy.loc[data_copy['m'] == 'b', ]  # we fix events in B
    btree = KDTree(B[['x', 'y','z']], leafsize=leafsize)
    dist, idx = btree.query(A[['x', 'y','z']], k=1)
    return dist_to_arclength(dist)

## Population Experiment

Compute inter-event distances from each event in A (month 0) to the nearest event in B (month 1) for all pairwise combinations of the individuals filtered above.

In [21]:
# dists = {}  # Dict{Dict{np.array}}... top level is A, second level B
# for a_id in keep:
#     for b_id in keep:
#         if a_id not in dists:
#             dists[a_id] = {}
#         if b_id in dists[a_id]:
#             continue
#         tmp = mpp.loc[ ((mpp.id == a_id) & (mpp.m == 'a')) |
#                        ((mpp.id == b_id) & (mpp.m == 'b')) ]
#         dists[a_id][b_id] = kdnearest(tmp)

# filepath = os.path.join("..", "data", "distances_month0a_month1b.pkl")
# with open(filepath, 'wb') as f:
#     pkl.dump(dists, f)

In [22]:
filepath = os.path.join("..", "data", "distances_month0a_month1b.pkl")
with open(filepath, 'rb') as f:
    dists = pkl.load(f)

In [23]:
def plot_distance_distn(user_id):
    """
    Plot the distance boxplots (same and diff) for a given user
    """
    uids = sorted(dists.keys())
    N = len(uids)

    # generate an array of rainbow colors by fixing the saturation and lightness
    # of the HSL representation of colour and marching around the hue. 
    c = ['hsl('+str(h)+',50%'+',50%)' for h in np.linspace(0, 360, N)]

    # Each box is represented by a dict that contains the data, type, and colour. 
    # Use list comprehension to describe N boxes, each with a different colour and 
    # with different randomly generated data:
    data = [
        {
            'x': dists.get(user_id).get(uids[i]), 
            'type': 'box',
            'marker':{'color': c[i] if user_id != uids[i] else 'black'},
            'name': 'User {}'.format(int(uids[i])),
            'boxpoints': False,
            'whiskerwidth': 0.5
        } for i in range(N)
    ]

    # format the layout
    layout = {
        'title': 'User {}'.format(int(user_id)),
#         'xaxis': {'showgrid':False,'zeroline':False, 'tickangle':60,'showticklabels':False},
#         'yaxis': {'zeroline':False,'gridcolor':'white'},
#         'paper_bgcolor': 'rgb(233,233,233)',
#         'plot_bgcolor': 'rgb(233,233,233)',
    }

    fig = go.Figure(data=data, layout=layout)
    
    iplot(fig, show_link=False)
    
    plot_figure(user_id)

In [24]:
#### examples
# 518  - consistent between months with some new locations
# 907  - very concentrated
# 13   - clustered w/ outliers
# 1587 - some clustering, visits popular spots
# 1725 - extreme clustering @ Disneyland.... will look liek every tourist!
# 23   - very dense, has a lot of events all over OC
# 1194 - all points at one location
# 11, 89, 1200, 1915  all visit a subset of the same exact locations
#     (Balboa & Saddleback College)
# 1953, 1954, 1957, 1962, 1969 all have very small diff-source distns 
#     (may be same account? variety of locations that are all the same)

uids = sorted(dists.keys())  # can choose any id from this list... there are 75
plot_distance_distn(1200)